PER CHI USA OANDA

Aggiornare tpqoa con:
<br>pip install git+git://github.com/yhilpisch/tpqoa

Se non hai git installato:
<br>Download git from https://git-scm.com/downloads
<br>pip uninstall tpqoa
<br>pip install git+git://github.com/yhilpisch/tpqoa

# Trader Class for OANDA

In [1]:
import pandas as pd
import numpy as np
import time
from datetime import datetime, timedelta, UTC

In [2]:
import tpqoa
api=tpqoa.tpqoa("oandaMY.cfg")

In [3]:
api.stream_data('EUR_USD',stop=10) 

2024-11-15T09:44:07.709211886Z 1.05694 1.05704
2024-11-15T09:44:10.636902354Z 1.0569 1.057
2024-11-15T09:44:11.318845966Z 1.05689 1.05698
2024-11-15T09:44:11.389745388Z 1.05689 1.05699
2024-11-15T09:44:12.620048075Z 1.0569 1.057
2024-11-15T09:44:13.173130837Z 1.05688 1.05698
2024-11-15T09:44:13.634123953Z 1.05688 1.05698
2024-11-15T09:44:14.997828439Z 1.05689 1.05699
2024-11-15T09:44:15.587410644Z 1.05689 1.05698
2024-11-15T09:44:15.752547886Z 1.05689 1.05699


In [4]:
api.stream_data??

Signature: api.stream_data(instrument, stop=None, ret=False, callback=None)
Source:   
    def stream_data(self, instrument, stop=None, ret=False, callback=None):
        ''' Starts a real-time data stream.

        Parameters
        instrument: string
            valid instrument name
        '''
        self.stream_instrument = instrument
        self.ticks = 0
        response = self.ctx_stream.pricing.stream(
            self.account_id, snapshot=True,
            instruments=instrument)
        msgs = []
        for msg_type, msg in response.parts():
            msgs.append(msg)
            # print(msg_type, msg)
            if msg_type == 'pricing.ClientPrice':
                self.ticks += 1
                self.time = msg.time
                if callback is not None:
                    callback(msg.instrument, msg.time,
                             float(msg.bids[0].dict()['price']),
                             float(msg.asks[0].dict()['price']))
                else:
      

In [5]:
api.on_success??

Signature: api.on_success(time, bid, ask)
Source:   
    def on_success(self, time, bid, ask):
        ''' Method called when new data is retrieved. '''
        print(time, bid, ask)
File:      c:\programdata\anaconda3\lib\site-packages\tpqoa\tpqoa.py
Type:      method

In [6]:
class Trader(tpqoa.tpqoa):
    def on_success(self, time, bid, ask):
        ''' Method called when new data is retrieved. '''
        print("Questa è la classe clone di tpqoa",time, bid, ask)

In [7]:
api2=Trader("oandaMY.cfg")

In [8]:
api2.stream_data('EUR_USD',stop=10) 

Questa è la classe clone di tpqoa 2024-11-15T09:44:15.752547886Z 1.05689 1.05699
Questa è la classe clone di tpqoa 2024-11-15T09:44:18.807751509Z 1.05689 1.05698
Questa è la classe clone di tpqoa 2024-11-15T09:44:20.655107829Z 1.05686 1.05696
Questa è la classe clone di tpqoa 2024-11-15T09:44:20.745054294Z 1.05687 1.05696
Questa è la classe clone di tpqoa 2024-11-15T09:44:27.636258176Z 1.05687 1.05695
Questa è la classe clone di tpqoa 2024-11-15T09:44:29.132422368Z 1.05687 1.05695
Questa è la classe clone di tpqoa 2024-11-15T09:44:33.094341891Z 1.05687 1.05696
Questa è la classe clone di tpqoa 2024-11-15T09:44:33.330028313Z 1.05688 1.05696
Questa è la classe clone di tpqoa 2024-11-15T09:44:34.111925703Z 1.05689 1.05698
Questa è la classe clone di tpqoa 2024-11-15T09:44:34.751001566Z 1.05689 1.05699


In [9]:
class Trader(tpqoa.tpqoa):
    
    def __init__(self,config_file):
        super().__init__(config_file)
        self.tickData = pd.DataFrame()
    
    def on_success(self, time, bid, ask):
        print(time, bid, ask)
        df = pd.DataFrame({"bid":bid,"ask":ask,"mid":(ask+bid)/2}, index=[pd.to_datetime(time)])
        self.tickData=pd.concat((self.tickData,df),axis=0)

In [10]:
api=Trader("oandaMY.cfg")

In [11]:
api.tickData

Empty DataFrame
Columns: []
Index: []

In [12]:
api.stream_data('EUR_USD',stop=10) 

2024-11-15T09:44:35.496047433Z 1.05689 1.05698
2024-11-15T09:44:35.850550546Z 1.05692 1.05701
2024-11-15T09:44:36.049130194Z 1.05691 1.05701
2024-11-15T09:44:36.577629981Z 1.05692 1.05702
2024-11-15T09:44:37.071674893Z 1.05693 1.05701
2024-11-15T09:44:37.361641884Z 1.05693 1.05701
2024-11-15T09:44:37.536479626Z 1.05693 1.05703
2024-11-15T09:44:39.073478929Z 1.05693 1.05702
2024-11-15T09:44:39.253098432Z 1.05693 1.05703
2024-11-15T09:44:39.693409550Z 1.05694 1.05703


In [13]:
api.tickData

bid      ask       mid
2024-11-15 09:44:35.496047433+00:00  1.05689  1.05698  1.056935
2024-11-15 09:44:35.850550546+00:00  1.05692  1.05701  1.056965
2024-11-15 09:44:36.049130194+00:00  1.05691  1.05701  1.056960
2024-11-15 09:44:36.577629981+00:00  1.05692  1.05702  1.056970
2024-11-15 09:44:37.071674893+00:00  1.05693  1.05701  1.056970
2024-11-15 09:44:37.361641884+00:00  1.05693  1.05701  1.056970
2024-11-15 09:44:37.536479626+00:00  1.05693  1.05703  1.056980
2024-11-15 09:44:39.073478929+00:00  1.05693  1.05702  1.056975
2024-11-15 09:44:39.253098432+00:00  1.05693  1.05703  1.056980
2024-11-15 09:44:39.693409550+00:00  1.05694  1.05703  1.056985

In [14]:
api.tickData.resample("1s",label="right").last()

bid      ask       mid
2024-11-15 09:44:36+00:00  1.05692  1.05701  1.056965
2024-11-15 09:44:37+00:00  1.05692  1.05702  1.056970
2024-11-15 09:44:38+00:00  1.05693  1.05703  1.056980
2024-11-15 09:44:39+00:00      NaN      NaN       NaN
2024-11-15 09:44:40+00:00  1.05694  1.05703  1.056985

In [15]:
api.tickData.resample("1s",label="right").last().ffill() # right significa che l'etichetta è a destra della larghezza, cioè alla fine del secondo

bid      ask       mid
2024-11-15 09:44:36+00:00  1.05692  1.05701  1.056965
2024-11-15 09:44:37+00:00  1.05692  1.05702  1.056970
2024-11-15 09:44:38+00:00  1.05693  1.05703  1.056980
2024-11-15 09:44:39+00:00  1.05693  1.05703  1.056980
2024-11-15 09:44:40+00:00  1.05694  1.05703  1.056985

In [16]:
class Trader(tpqoa.tpqoa):
    
    def __init__(self,config_file, instrument, period):
        super().__init__(config_file)
        self.instrument = instrument
        self.period=period
        self.tickData = pd.DataFrame()
    
    def on_success(self, time, bid, ask):
#        print(time, bid, ask)
        print(self.ticks, end=" ")
        df = pd.DataFrame({"bid":bid,"ask":ask,"mid":(ask+bid)/2}, index=[pd.to_datetime(time)])
        self.tickData=pd.concat((self.tickData,df),axis=0)
        self.resampleJoin()
    
    def resampleJoin(self):
        self.rawData=self.tickData.resample(self.period,label="right").last().ffill().iloc[:-1] 
        # con iloc[:-1] eliminiamo l'ultimo intervallo in quanto incompleto

In [17]:
api=Trader("oandaMY.cfg","EUR_USD","5s")

In [18]:
api.stream_data("EUR_USD",stop=40) 

1 2 3 4 5 6 7 8 9 10 11 12 13 14 15 16 17 18 19 20 21 22 23 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 

In [19]:
api.rawData

bid      ask       mid
2024-11-15 09:44:40+00:00  1.05694  1.05703  1.056985
2024-11-15 09:44:45+00:00  1.05693  1.05702  1.056975
2024-11-15 09:44:50+00:00  1.05694  1.05703  1.056985
2024-11-15 09:44:55+00:00  1.05692  1.05701  1.056965
2024-11-15 09:45:00+00:00  1.05693  1.05703  1.056980
2024-11-15 09:45:05+00:00  1.05682  1.05692  1.056870
2024-11-15 09:45:10+00:00  1.05682  1.05691  1.056865

## Migliorare l'efficienza del resampling

Fare un resample di tutti i dati ad ogni tick è molto inefficiente. In realtà, quando abbiamo completato un intervallo, possiamo farne un resample definitivo e non rifarlo più.

Ad esempio, se abbiamo 5 secondi di periodo, quando riceviamo un tick che è **oltre** 5 secondi dall'ultimo periodo valido, allora abbiamo concluso un nuovo periodo e facciamo un resample.

- 10:55:24.00 --> tempo dell'ultimoPeriodo
- 10:55:27
- 10:55:27
- 10:55:28
- 10:55:29.07 --> è oltre 5 secondi l'ultimo periodo, quindi è appena finito un periodo. Il tempo dell'ultimoPeriodo diventa quello immediatamente prima 10:55:29.00 e facciamo un resample


### Una parentesi sulla gestione delle date e dei tempi

In [20]:
datetime.now(UTC)

datetime.datetime(2024, 11, 15, 9, 45, 11, 318708, tzinfo=datetime.timezone.utc)

In [21]:
pd.to_datetime(datetime.now(UTC))

Timestamp('2024-11-15 09:45:11.325884+0000', tz='UTC')

In [22]:
pd.to_datetime(datetime.now(UTC))  - pd.to_datetime("2021-11-10 10:10:00").tz_localize("UTC")

Timedelta('1100 days 23:35:11.335077')

In [23]:
pd.to_timedelta("5s")

Timedelta('0 days 00:00:05')

In [24]:
pd.to_datetime(datetime.now(UTC))  - pd.to_datetime("2021-11-10 10:10:00").tz_localize("UTC") > pd.to_timedelta("5s")

True

In [25]:
class Trader(tpqoa.tpqoa):
    
    def __init__(self,config_file, instrument, period):
        super().__init__(config_file)
        self.instrument = instrument
        self.period=period
        self.tickData = pd.DataFrame()
        # UTC time quando inizializzo. Questo serve SOLO per avere un valore ad ultimoPeriodo altrimenti dà errore dopo
        self.ultimoPeriodo = pd.to_datetime(datetime.now(UTC))
    
    def on_success(self, time, bid, ask):
#        print(time, bid, ask)
        print(self.ticks, end=" ")
        tickCorrente = pd.to_datetime(time)
        df = pd.DataFrame({"bid":bid,"ask":ask,"mid":(ask+bid)/2}, index=[pd.to_datetime(time)])
        self.tickData=pd.concat((self.tickData,df),axis=0)
        if tickCorrente - self.ultimoPeriodo > pd.to_timedelta(self.period): # converto il 5s in un intervallo temporale
            self.resampleJoin()
    
    def resampleJoin(self):
        self.rawData=self.tickData.resample(self.period,label="right").last().ffill().iloc[:-1] 
        # con iloc[:-1] eliminiamo l'ultimo intervallo in quanto incompleto
        self.ultimoPeriodo = self.rawData.index[-1] # UTC time dell'ultimo periodo valido

In [26]:
api=Trader("oandaMY.cfg","EUR_USD","5s")
api.stream_data("EUR_USD",stop=40) 

1 2 3 4 5 6 7 8 9 10 11 12 13 14 15 16 17 18 19 20 21 22 23 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 

In [27]:
api.rawData

bid      ask       mid
2024-11-15 09:45:15+00:00  1.05681  1.05690  1.056855
2024-11-15 09:45:20+00:00  1.05682  1.05692  1.056870
2024-11-15 09:45:25+00:00  1.05683  1.05692  1.056875
2024-11-15 09:45:30+00:00  1.05674  1.05682  1.056780
2024-11-15 09:45:35+00:00  1.05676  1.05686  1.056810
2024-11-15 09:45:40+00:00  1.05673  1.05683  1.056780
2024-11-15 09:45:45+00:00  1.05673  1.05681  1.056770

Ora:
- buttiamo via tutti i tick che sono completi e hanno già fatto un resample, così non sprechiamo spazio e non rifacciamo il resample ogni volta
- ogni volta che facciamo resample dobbiamo APPENDERE ai dati che già abbiamo e non sovrascrivere, dato che abbiamo buttato via i dati vecchi

In [28]:
class Trader(tpqoa.tpqoa):
    
    def __init__(self,config_file, instrument, period):
        super().__init__(config_file)
        self.instrument = instrument
        self.period=period
        self.tickData = pd.DataFrame()
        self.rawData = pd.DataFrame()
        # UTC time quando inizializzo. Questo serve SOLO per avere un valore ad ultimoPeriodo altrimenti dà errore dopo
        self.ultimoPeriodo = pd.to_datetime(datetime.now(UTC))
    
    def on_success(self, time, bid, ask):
#        print(time, bid, ask)
        print(self.ticks, end=" ")
        tickCorrente = pd.to_datetime(time)
        df = pd.DataFrame({"bid":bid,"ask":ask,"mid":(ask+bid)/2}, index=[pd.to_datetime(time)])
        self.tickData=pd.concat((self.tickData,df),axis=0)
        if tickCorrente - self.ultimoPeriodo > pd.to_timedelta(self.period): # converto il 5s in un intervallo temporale
            self.resampleJoin()
    
    def resampleJoin(self):
        self.rawData=pd.concat((self.rawData,self.tickData.resample(self.period,label="right").last().ffill().iloc[:-1] ),axis=0)
        # appendiamo ai dati che già abbiamo invece di sovrascrivere
        self.tickData = self.tickData.iloc[-1:] 
        # teniamo soltanto l'ultimo, quello che ha fatto scattare il resample e quindi è il primo del periodo nuovo
        # uso anche i : perché così mantiene il dataframe, altrimenti me lo converte in un series 
        self.ultimoPeriodo = self.rawData.index[-1] 

In [29]:
api=Trader("oandaMY.cfg","EUR_USD","5s")
api.stream_data("EUR_USD",stop=40) 

1 2 3 4 5 6 7 8 9 10 11 12 13 14 15 16 17 18 19 20 21 22 23 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 

In [30]:
api.rawData

bid      ask       mid
2024-11-15 09:45:50+00:00  1.05670  1.05680  1.056750
2024-11-15 09:45:55+00:00  1.05668  1.05677  1.056725
2024-11-15 09:46:00+00:00  1.05663  1.05673  1.056680
2024-11-15 09:46:05+00:00  1.05668  1.05679  1.056735
2024-11-15 09:46:10+00:00  1.05663  1.05673  1.056680
2024-11-15 09:46:15+00:00  1.05663  1.05672  1.056675
2024-11-15 09:46:20+00:00  1.05664  1.05673  1.056685